In [1]:
import warnings
warnings.filterwarnings('ignore')

import geopandas as gpd
import pandas as pd
import shapely
from shapely.geometry import Polygon, Point
import geopy.distance
import pandana
import numpy as np
import requests
import folium

In [2]:
stroke_facs = pd.read_csv('stroke_facs_latest.csv')

In [3]:
stroke_facs = stroke_facs[['Name_English','Facility name-VN','Type_name','address','longitude','latitude',
                           'pro_name_e','dist_name_e']].reset_index()


stroke_facs.rename(columns={'index':'fac_id'},inplace=True)

In [4]:
stroke_facs['longitude'] = stroke_facs['longitude'].astype(float)
stroke_facs['latitude'] = stroke_facs['latitude'].astype(float)


In [30]:
stroke_facs.head(2)

fac_id                           Name_English  \
0       0  Saint Paul Municipal General Hospital   
1       1    Viet Duc (University) Hospital (CS1   

                           Facility name-VN                     Type_name  \
0                Bệnh viện đa khoa Xanh Pôn   provincial general hospital   
1  Bệnh viện Hữu nghị Việt Đức (CS1 Hà Nội)  Central specialized hospital   

                                             address   longitude   latitude  \
0  12 Chu Văn An, Phường Điện Biên, Quận Ba Đình,...  105.835586  21.031610   
1   40 Tràng Thi, P. Hàng Bông, Q. Hoàn Kiếm, Hà Nội  105.845353  21.029563   

  pro_name_e         dist_name_e  \
0     Ha Noi    Ba Dinh District   
1     Ha Noi  Hoan Kiem District   

                                    isochrone_30mins  \
0  [{'properties': {'fill-opacity': 0.33, 'fillCo...   
1  [{'properties': {'fill-opacity': 0.33, 'fillCo...   

                                    isochrone_60mins  \
0  [{'properties': {'fill-opacity': 0.33, 'fillCo...   
1  [{'properties': {'fill-opacity': 0.33, 'fillCo...   

                                              30mins  \
0  POLYGON ((105.835586 21.199413, 105.834999 21....   
1  POLYGON ((105.821353 21.169769, 105.821037 21....   

                                              60mins  \
0  POLYGON ((105.891586 21.427823, 105.887586 21....   
1  POLYGON ((105.889353 21.391684, 105.887404 21....   

                                           ID_30mins  \
0  [116236, 116237, 116238, 116239, 116240, 11624...   
1  [116236, 116237, 116238, 116239, 116240, 11624...   

                                           ID_60mins  
0  [90115, 90116, 90119, 122894, 122895, 122896, ...  
1  [90115, 122893, 122894, 122895, 122896, 122897...

In [5]:
len(stroke_facs)

106

In [6]:
population = pd.read_csv(r'ppp_VNM_2020_1km_Aggregated_UNadj.csv').reset_index()
population.columns = ['ID','xcoord','ycoord','household_count']
population['xcoord'] = population['xcoord'].round(2)
population['ycoord'] = population['ycoord'].round(2)

population = population.groupby(['xcoord','ycoord'])['household_count'].sum().reset_index().reset_index()
population['household_count'] = population['household_count'].round()
population.columns = ['ID','xcoord','ycoord','population']

population_worldpop = gpd.GeoDataFrame(population, 
                                       geometry=gpd.points_from_xy(x=population.xcoord, 
                                                                   y=population.ycoord))

print('Total Population:',round(population_worldpop['population'].sum()/1000000,2),'million')

Total Population: 97.34 million


In [28]:
len(population_worldpop)

283557

In [7]:
%%time

facebook_pop_csv = pd.read_csv('vnm_general_2020.csv')
population = facebook_pop_csv[['latitude','longitude','vnm_general_2020']].reset_index()
population.columns = ['ID','ycoord','xcoord','population']

population_meta = gpd.GeoDataFrame(population, 
                                       geometry=gpd.points_from_xy(x=population.xcoord, 
                                                                   y=population.ycoord))
gadm_vnm = gpd.read_file('gadm41_VNM_shp/gadm41_VNM_0.shp')
population_meta = gpd.sjoin(population_meta, gadm_vnm, op='within')
print('Total Population:',round(population_meta['population'].sum()/1000000,2),'million')


Total Population: 97.29 million
CPU times: user 43.6 s, sys: 17.9 s, total: 1min 1s
Wall time: 1min 5s


In [29]:
len(population_meta)

21143695

In [8]:
access_token = "Enter MapBox API Key Here"

In [9]:
def get_isochrone(df,minutes_list,access_token,mode):
    longitude = df['longitude']
    latitude = df['latitude']
    query = """https://api.mapbox.com/isochrone/v1/mapbox/"""
    query = query+mode+'/'
    query = query+str(longitude)+','+str(latitude)+'?'
    query = query+'contours_minutes='+minutes_list
    query = query+'&polygons=true&access_token='
    query = query+access_token
    req_return = (requests.get(query).json())
    
    if('code' in req_return):
        if (req_return['code']=='NoSegment'):
            print('No Segment')
        else:
            print(req_return)     
    else:
        #print(req_return)     
        return(req_return['features'])

In [10]:
def get_pop_count(population_df,x):
    pop_count = population_df[population_df['ID'].isin(x)]['population'].sum()
    return pop_count

In [11]:
%%time

stroke_facs['isochrone_30mins'] = stroke_facs[['longitude','latitude']].apply(get_isochrone,
                                                                                   minutes_list="30",
                                                                                   access_token=access_token,
                                                                                   mode='driving',
                                                                                   axis=1)

stroke_facs['isochrone_60mins'] = stroke_facs[['longitude','latitude']].apply(get_isochrone,
                                                                                   minutes_list="60",
                                                                                   access_token=access_token,
                                                                                   mode='driving',
                                                                                   axis=1)

stroke_facs['30mins'] = stroke_facs['isochrone_30mins'].apply(lambda x: x[0]['geometry'])
stroke_facs['30mins'] = stroke_facs['30mins'].apply(lambda x:Polygon(x['coordinates'][0]))

stroke_facs['60mins'] = stroke_facs['isochrone_60mins'].apply(lambda x: x[0]['geometry'])
stroke_facs['60mins'] = stroke_facs['60mins'].apply(lambda x:Polygon(x['coordinates'][0]))


CPU times: user 3.61 s, sys: 536 ms, total: 4.15 s
Wall time: 19.5 s


In [12]:
def get_population_within_vector(vector_polygon,vector_layer):
    pip_mask = vector_layer.within(vector_polygon)
    pip_data = vector_layer.loc[pip_mask]
    return(list(pip_data['ID'].unique()))


In [13]:
## Change Population Here

population_selected = population_worldpop

In [14]:
%%time

df_30mins = stroke_facs[['30mins','fac_id']]
df_30mins.columns = ['geometry','fac_id']
df_30mins = gpd.GeoDataFrame(df_30mins)
join30mins = gpd.sjoin(population_selected[['ID','geometry']],df_30mins,predicate='within')[['ID','fac_id']]
join30mins = join30mins.groupby('fac_id')['ID'].agg(list).reset_index()
join30mins['ID'] = join30mins['ID'].apply(lambda x:list(set(x)))
join30mins.columns = ['fac_id','ID_30mins']


CPU times: user 238 ms, sys: 133 ms, total: 371 ms
Wall time: 393 ms


In [15]:
%%time

df_60mins = stroke_facs[['60mins','fac_id']]
df_60mins.columns = ['geometry','fac_id']
df_60mins = gpd.GeoDataFrame(df_60mins)
join60mins = gpd.sjoin(population_selected[['ID','geometry']],df_60mins,predicate='within')[['ID','fac_id']]
join60mins = join60mins.groupby('fac_id')['ID'].agg(list).reset_index()
join60mins['ID'] = join60mins['ID'].apply(lambda x:list(set(x)))
join60mins.columns = ['fac_id','ID_60mins']

CPU times: user 397 ms, sys: 64.2 ms, total: 461 ms
Wall time: 464 ms


In [16]:
stroke_facs = pd.merge(stroke_facs,join30mins, on='fac_id')
stroke_facs = pd.merge(stroke_facs,join60mins, on='fac_id')

In [17]:
stroke_facs.head(2)

fac_id                           Name_English  \
0       0  Saint Paul Municipal General Hospital   
1       1    Viet Duc (University) Hospital (CS1   

                           Facility name-VN                     Type_name  \
0                Bệnh viện đa khoa Xanh Pôn   provincial general hospital   
1  Bệnh viện Hữu nghị Việt Đức (CS1 Hà Nội)  Central specialized hospital   

                                             address   longitude   latitude  \
0  12 Chu Văn An, Phường Điện Biên, Quận Ba Đình,...  105.835586  21.031610   
1   40 Tràng Thi, P. Hàng Bông, Q. Hoàn Kiếm, Hà Nội  105.845353  21.029563   

  pro_name_e         dist_name_e  \
0     Ha Noi    Ba Dinh District   
1     Ha Noi  Hoan Kiem District   

                                    isochrone_30mins  \
0  [{'properties': {'fill-opacity': 0.33, 'fillCo...   
1  [{'properties': {'fill-opacity': 0.33, 'fillCo...   

                                    isochrone_60mins  \
0  [{'properties': {'fill-opacity': 0.33, 'fillCo...   
1  [{'properties': {'fill-opacity': 0.33, 'fillCo...   

                                              30mins  \
0  POLYGON ((105.835586 21.199413, 105.834999 21....   
1  POLYGON ((105.821353 21.169769, 105.821037 21....   

                                              60mins  \
0  POLYGON ((105.891586 21.427823, 105.887586 21....   
1  POLYGON ((105.889353 21.391684, 105.887404 21....   

                                           ID_30mins  \
0  [116236, 116237, 116238, 116239, 116240, 11624...   
1  [116236, 116237, 116238, 116239, 116240, 11624...   

                                           ID_60mins  
0  [90115, 90116, 90119, 122894, 122895, 122896, ...  
1  [90115, 122893, 122894, 122895, 122896, 122897...

In [18]:
start_coords = (14.0583, 108.2772)
folium_map = folium.Map(location=start_coords, zoom_start=5)

test_ids = stroke_facs

for i in range(0,len(test_ids)):
    folium.Marker([test_ids.iloc[i]['latitude'], test_ids.iloc[i]['longitude']],
                        color='blue',popup=test_ids.iloc[i]['Name_English']).add_to(folium_map)
    
    geo_j = folium.GeoJson(data=test_ids.iloc[i]['60mins'],style_function=lambda x:{'color': 'blue'})
    folium.Popup(test_ids.iloc[i]['Name_English']).add_to(geo_j)
    geo_j.add_to(folium_map)
    
    geo_j = folium.GeoJson(data=test_ids.iloc[i]['30mins'],style_function=lambda x:{'color': 'purple'})
    folium.Popup(test_ids.iloc[i]['Name_English']).add_to(geo_j)
    geo_j.add_to(folium_map)
    

# Define the URL template for the Mapbox basemap
mapbox_url = f'https://api.mapbox.com/styles/v1/mapbox/{{id}}/tiles/{{z}}/{{x}}/{{y}}?access_token={access_token}'
mapbox_basemap = folium.TileLayer(tiles=mapbox_url, attr='Mapbox', name='Mapbox Bright', max_zoom=20, id='mapbox/light-v10')

# Add the Mapbox basemap as a baselayer to the map
mapbox_basemap.add_to(folium_map)

# Create a custom HTML legend
legend_html = '''
     <div style="position: fixed; 
                 bottom: 50px; left: 50px; width: 180px; height: 90px; 
                 border:2px solid grey; z-index:9999; font-size:14px;
                 background-color: white;
                 ">&nbsp;<b>Legend (Isodistances)</b><br>
         &nbsp;<i class="fa fa-square" style="color:blue"></i>&nbsp; 60 mins driving<br>
         &nbsp;<i class="fa fa-square" style="color:purple"></i>&nbsp; 30 mins driving<br>
      </div>
     '''

# Add the custom legend as a separate layer to the map
folium_map.get_root().html.add_child(folium.Element(legend_html))

heading_html = '''
     <div style="position: absolute; 
                 top: 50px; left: 50px; width: 220px; height: 50px; 
                 border: none; z-index:9999; font-size: 15px;
                 background-color: rgba(255, 255, 255, 0.6);
                 ">&nbsp;<b>Stroke Facility Catchment Area </b><br>
      </div>
     '''

# Add the custom heading as a separate layer to the map
folium_map.get_root().html.add_child(folium.Element(heading_html))

folium_map


In [19]:
%%time

list_pop_ids = list(stroke_facs['ID_60mins'].values)
list_pop_ids = [item for sublist in list_pop_ids for item in sublist]
pop_with_access = list(set(list_pop_ids))

(population_selected[population_selected['ID'].isin(pop_with_access)]['population'].sum()*100/population_selected['population'].sum()).round()


CPU times: user 39.1 ms, sys: 16.5 ms, total: 55.6 ms
Wall time: 55.9 ms


68.0

In [20]:
%%time

list_pop_ids = list(stroke_facs['ID_30mins'].values)
list_pop_ids = [item for sublist in list_pop_ids for item in sublist]
pop_with_access = list(set(list_pop_ids))

(population_selected[population_selected['ID'].isin(pop_with_access)]['population'].sum()*100/population_selected['population'].sum()).round()


CPU times: user 15.1 ms, sys: 1.91 ms, total: 17 ms
Wall time: 15.8 ms


40.0

In [21]:
%%time 

health_facilities_node = gpd.read_file('healthsites/Vietnam-node.shp')
health_facilities_node.crs = "EPSG:4326"

health_facilities_way = gpd.read_file('healthsites/Vietnam-way.shp')
health_facilities_way.crs = "EPSG:4326"
health_facilities_way = health_facilities_way.to_crs('EPSG:32752')
health_facilities_way['geometry'] = health_facilities_way['geometry'].centroid
health_facilities_way = health_facilities_way.to_crs('EPSG:4326')

health_sites = pd.concat([health_facilities_node,health_facilities_way])
health_sites = health_sites[['osm_id','amenity','name','geometry']]
health_sites['latitude'] = health_sites['geometry'].apply(lambda x:x.y)
health_sites['longitude'] = health_sites['geometry'].apply(lambda x:x.x)

health_sites = health_sites.reset_index()
health_sites.rename(columns={'index':'Hosp_ID'},inplace=True)

health_sites = health_sites[health_sites['amenity'].isin(['hospital'])]

CPU times: user 1.17 s, sys: 53 ms, total: 1.22 s
Wall time: 1.26 s


In [32]:
health_sites['Hosp_ID'].nunique()

1013

In [22]:
%%time

health_sites['isochrone_30mins'] = health_sites[['longitude','latitude']].apply(get_isochrone,
                                                                                   minutes_list="30",
                                                                                   access_token=access_token,
                                                                                   mode='driving',
                                                                                   axis=1)

health_sites['isochrone_60mins'] = health_sites[['longitude','latitude']].apply(get_isochrone,
                                                                                   minutes_list="60",
                                                                                   access_token=access_token,
                                                                                   mode='driving',
                                                                                   axis=1)

health_sites['30mins'] = health_sites['isochrone_30mins'].apply(lambda x: x[0]['geometry'])
health_sites['30mins'] = health_sites['30mins'].apply(lambda x:Polygon(x['coordinates'][0]))

health_sites['60mins'] = health_sites['isochrone_60mins'].apply(lambda x: x[0]['geometry'])
health_sites['60mins'] = health_sites['60mins'].apply(lambda x:Polygon(x['coordinates'][0]))


CPU times: user 38.2 s, sys: 3.8 s, total: 42 s
Wall time: 4min 43s


In [23]:
%%time

df_30mins = health_sites[['30mins','Hosp_ID']]
df_30mins.columns = ['geometry','Hosp_ID']
df_30mins = gpd.GeoDataFrame(df_30mins)
join30mins = gpd.sjoin(population_selected[['ID','geometry']],df_30mins,predicate='within')[['ID','Hosp_ID']]
join30mins = join30mins.groupby('Hosp_ID')['ID'].agg(list).reset_index()
join30mins['ID'] = join30mins['ID'].apply(lambda x:list(set(x)))
join30mins.columns = ['Hosp_ID','ID_30mins']


CPU times: user 624 ms, sys: 89.5 ms, total: 713 ms
Wall time: 713 ms


In [24]:
%%time

df_60mins = health_sites[['60mins','Hosp_ID']]
df_60mins.columns = ['geometry','Hosp_ID']
df_60mins = gpd.GeoDataFrame(df_60mins)
join60mins = gpd.sjoin(population_selected[['ID','geometry']],df_60mins,predicate='within')[['ID','Hosp_ID']]
join60mins = join60mins.groupby('Hosp_ID')['ID'].agg(list).reset_index()
join60mins['ID'] = join60mins['ID'].apply(lambda x:list(set(x)))
join60mins.columns = ['Hosp_ID','ID_60mins']

CPU times: user 2.13 s, sys: 352 ms, total: 2.49 s
Wall time: 2.49 s


In [25]:
health_sites = pd.merge(health_sites,join30mins, on='Hosp_ID')
health_sites = pd.merge(health_sites,join60mins, on='Hosp_ID')

In [26]:
%%time

list_pop_ids = list(health_sites['ID_60mins'].values)
list_pop_ids = [item for sublist in list_pop_ids for item in sublist]
pop_with_access = list(set(list_pop_ids))

(population_selected[population_selected['ID'].isin(pop_with_access)]['population'].sum()*100/population_selected['population'].sum()).round()


CPU times: user 157 ms, sys: 20.7 ms, total: 177 ms
Wall time: 177 ms


87.0

In [27]:
%%time

list_pop_ids = list(health_sites['ID_30mins'].values)
list_pop_ids = [item for sublist in list_pop_ids for item in sublist]
pop_with_access = list(set(list_pop_ids))

(population_selected[population_selected['ID'].isin(pop_with_access)]['population'].sum()*100/population_selected['population'].sum()).round()


CPU times: user 57.7 ms, sys: 4.79 ms, total: 62.5 ms
Wall time: 61.3 ms


69.0

In [33]:
health_sites.head(2)

Hosp_ID      osm_id   amenity                         name  \
0        0  1612954364  hospital                         None   
1        0   410573788  hospital  Trung tâm Y tế huyện Đất Đỏ   

                     geometry   latitude   longitude  \
0  POINT (108.09622 10.93367)  10.933668  108.096216   
1  POINT (107.27461 10.46449)  10.464487  107.274614   

                                    isochrone_30mins  \
0  [{'properties': {'fill-opacity': 0.33, 'fillCo...   
1  [{'properties': {'fill-opacity': 0.33, 'fillCo...   

                                    isochrone_60mins  \
0  [{'properties': {'fill-opacity': 0.33, 'fillCo...   
1  [{'properties': {'fill-opacity': 0.33, 'fillCo...   

                                              30mins  \
0  POLYGON ((108.202216 11.109697, 108.201357 11....   
1  POLYGON ((107.294614 10.65267, 107.293984 10.6...   

                                              60mins  \
0  POLYGON ((108.412216 11.257759, 108.40482 11.2...   
1  POLYGON ((107.366614 10.836147, 107.362614 10....   

                                           ID_30mins  \
0  [241673, 229386, 229387, 229388, 229389, 22939...   
1  [241673, 229386, 229387, 229388, 229389, 22939...   

                                           ID_60mins  
0  [229376, 229377, 229378, 229379, 229380, 22938...  
1  [229376, 229377, 229378, 229379, 229380, 22938...